## All the imports and settings

In [1]:
import os

!!! Пришлось понизить версию питона до 3.7:
```
conda install python=3.7
```

In [2]:
os.environ['JAVA_HOME']='/usr/lib/jvm/java-1.8.0-openjdk-amd64'
os.environ['PATH'] = os.environ['PATH'] + f':{os.environ["JAVA_HOME"]}/bin'
os.environ['JAVA_OPTION'] = '-Xmx48g'

In [3]:
import hail as hl
from bokeh.io import output_notebook, show

/home/barbitoff/.conda/envs/hail/lib/python3.6/site-packages/requests/__init__.py:91: RequestsDependencyWarning: urllib3 (1.26.4) or chardet (3.0.4) doesn't match a supported version!
  RequestsDependencyWarning)


In [4]:
hl.init(spark_conf={"spark.driver.memory": "100g"})
output_notebook()
# update-java-alternat

Running on Apache Spark version 2.4.1
SparkUI available at http://217.148.215.30:4041
Welcome to
     __  __     <>__
    / /_/ /__  __/ /
   / __  / _ `/ / /
  /_/ /_/\_,_/_/_/   version 0.2.63-cb767a7507c8
LOGGING: writing to /media/array/guar_proj/guar_snv/hail-20210824-0938-0.2.63-cb767a7507c8.log


Loading BokehJS ...

## FILENAMES


In [11]:
REF_NAME = "GUAR_RG"
REF_FILE = "/media/array/guar_proj/reference_masurca/assembly_guar_Masurca1.fasta"
REF_INDEX_FILE = "/media/array/guar_proj/reference_masurca/assembly_guar_Masurca1.fasta.fai"

INPUT_VCF = "/media/array/guar_proj/production_callset/GUAR_2of3_AF5pct.vcf"
INPUT_TSV = '/media/array/guar_proj/guar_snv/new_genius_pheno.tsv'

GWAS_EXPORT = 'output_pvals/filtered_gwas_LMM_'
PCA_SCORES = 'out_pc_scores/guar_filtered.pc_scores.csv'
OUT_VCF = 'out_vcf/guar_filtered_MAF_highconf.vcf'
LMM_OUTPUT = 'LMM_output'

### Import data from VCF

In [6]:
ref_g = hl.genetics.ReferenceGenome.from_fasta_file(REF_NAME, 
                                                    REF_FILE, 
                                                    REF_INDEX_FILE)

In [7]:
mt = hl.import_vcf(INPUT_VCF, reference_genome=ref_g)
mt = mt.annotate_cols(genome_id=hl.str(mt.s))
mt = mt.key_cols_by("genome_id")
mt = mt.drop("s")
mt.describe()

----------------------------------------
Global fields:
    None
----------------------------------------
Column fields:
    'genome_id': str
----------------------------------------
Row fields:
    'locus': locus<GUAR_RG>
    'alleles': array<str>
    'rsid': str
    'qual': float64
    'filters': set<str>
    'info': struct {
        AC: array<int32>, 
        AF: array<float64>, 
        AN: int32, 
        BaseQRankSum: float64, 
        DP: int32, 
        DS: bool, 
        END: int32, 
        ExcessHet: float64, 
        FS: float64, 
        InbreedingCoeff: float64, 
        MLEAC: array<int32>, 
        MLEAF: array<float64>, 
        MQ: float64, 
        MQRankSum: float64, 
        QD: float64, 
        RAW_MQandDP: array<int32>, 
        ReadPosRankSum: float64, 
        SOR: float64, 
        NGSEP_NHET: array<int32>, 
        NGSEP_NALT: array<int32>, 
        NGSEP_AF: array<float64>, 
        TASSEL_NHET: array<int32>, 
        TASSEL_NALT: array<int32>, 
        TAS

In [8]:
mt.count()

2021-08-24 09:39:12 Hail: INFO: Coerced sorted dataset


(5234, 166)

## Annotation

In [12]:
sa = hl.import_table(INPUT_TSV,
                      key='id', 
                      missing='',)
# Если надо какой-то столбец конвертировать, то делается это так:
sa = sa.annotate(genome_id = hl.str(sa['id']))
sa = sa.annotate(height = hl.float(sa['height']))
sa = sa.annotate(branch_height = hl.float(sa['branch_height']))
sa = sa.annotate(pod_number = hl.float(sa['pod_number']))
sa = sa.annotate(maturation_pct = hl.float(sa['maturation_pct']))
sa = sa.annotate(mature_pod_seed_weight = hl.float(sa['mature_pod_seed_weight']))
sa = sa.key_by('genome_id')
sa.describe()
sa.height.show()

2021-08-24 09:39:51 Hail: INFO: Reading table without type imputation
  Loading field 'id' as type str (not specified)
  Loading field 'height' as type str (not specified)
  Loading field 'branch_height' as type str (not specified)
  Loading field 'pod_number' as type str (not specified)
  Loading field 'maturation_pct' as type str (not specified)
  Loading field 'mature_pod_seed_weight' as type str (not specified)


----------------------------------------
Global fields:
    None
----------------------------------------
Row fields:
    'id': str 
    'height': float64 
    'branch_height': float64 
    'pod_number': float64 
    'maturation_pct': float64 
    'mature_pod_seed_weight': float64 
    'genome_id': str 
----------------------------------------
Key: ['genome_id']
----------------------------------------


2021-08-24 09:39:51 Hail: INFO: Ordering unsorted dataset with network shuffle


+-----------+-----------+
| genome_id |    height |
+-----------+-----------+
| str       |   float64 |
+-----------+-----------+
| "S1"      | -4.76e-01 |
| "S10"     |  6.45e-01 |
| "S100"    |  6.94e-01 |
| "S101"    | -1.64e+00 |
| "S102"    | -1.31e-01 |
| "S104"    | -1.05e-01 |
| "S105"    |  3.48e-01 |
| "S106"    | -1.45e-01 |
| "S107"    |  5.97e-01 |
| "S109"    | -1.06e+00 |
| "S11"     |  7.45e-01 |
| "S110"    |  6.78e-01 |
| "S111"    |  1.30e+00 |
| "S112"    |  1.18e+00 |
| "S113"    |  1.64e+00 |
| "S114"    |  1.18e-01 |
+-----------+-----------+
showing top 16 rows

In [13]:
mt = mt.annotate_cols(pheno = sa[mt.genome_id])
#mt.annotate_cols(genome_id_frmt=hl.str(mt.genome_id))
mt.describe()

----------------------------------------
Global fields:
    None
----------------------------------------
Column fields:
    'genome_id': str
    'pheno': struct {
        id: str, 
        height: float64, 
        branch_height: float64, 
        pod_number: float64, 
        maturation_pct: float64, 
        mature_pod_seed_weight: float64
    }
----------------------------------------
Row fields:
    'locus': locus<GUAR_RG>
    'alleles': array<str>
    'rsid': str
    'qual': float64
    'filters': set<str>
    'info': struct {
        AC: array<int32>, 
        AF: array<float64>, 
        AN: int32, 
        BaseQRankSum: float64, 
        DP: int32, 
        DS: bool, 
        END: int32, 
        ExcessHet: float64, 
        FS: float64, 
        InbreedingCoeff: float64, 
        MLEAC: array<int32>, 
        MLEAF: array<float64>, 
        MQ: float64, 
        MQRankSum: float64, 
        QD: float64, 
        RAW_MQandDP: array<int32>, 
        ReadPosRankSum: float64, 
  

In [14]:
#### Работает?
mt.entries().show(3)

2021-08-24 09:40:09 Hail: WARN: entries(): Resulting entries table is sorted by '(row_key, col_key)'.
    To preserve row-major matrix table order, first unkey columns with 'key_cols_by()'
2021-08-24 09:40:09 Hail: INFO: Coerced sorted dataset


+-------------------+------------+------+----------+----------+--------------+----------------+---------+-------------------+---------+
| locus             | alleles    | rsid |     qual | filters  | info.AC      | info.AF        | info.AN | info.BaseQRankSum | info.DP |
+-------------------+------------+------+----------+----------+--------------+----------------+---------+-------------------+---------+
| locus<GUAR_RG>    | array<str> | str  |  float64 | set<str> | array<int32> | array<float64> |   int32 |           float64 |   int32 |
+-------------------+------------+------+----------+----------+--------------+----------------+---------+-------------------+---------+
| contig_1004:28957 | ["C","T"]  | NA   | 2.00e+04 | NA       | [138]        | [3.73e-01]     |     370 |          3.49e-01 |    1079 |
| contig_1004:28957 | ["C","T"]  | NA   | 2.00e+04 | NA       | [138]        | [3.73e-01]     |     370 |          3.49e-01 |    1079 |
| contig_1004:28957 | ["C","T"]  | NA   | 2.00e+04 | NA       | [138]        | [3.73e-01]     |     370 |          3.49e-01 |    1079 |
+-------------------+------------+------+----------+----------+--------------+----------------+---------+-------------------+---------+

+---------+----------+----------------+----------+----------------------+--------------+----------------+----------+----------------+
| info.DS | info.END | info.ExcessHet |  info.FS | info.InbreedingCoeff | info.MLEAC   | info.MLEAF     |  info.MQ | info.MQRankSum |
+---------+----------+----------------+----------+----------------------+--------------+----------------+----------+----------------+
|    bool |    int32 |        float64 |  float64 |              float64 | array<int32> | array<float64> |  float64 |        float64 |
+---------+----------+----------------+----------+----------------------+--------------+----------------+----------+----------------+
|   false |       NA |      -0.00e+00 | 0.00e+00 |             4.67e-01 | [155]        | [4.19e-01]     | 6.00e+01 |       0.00e+00 |
|   false |       NA |      -0.00e+00 | 0.00e+00 |             4.67e-01 | [155]        | [4.19e-01]     | 6.00e+01 |       0.00e+00 |
|   false |       NA |      -0.00e+00 | 0.00e+00 |             4.67e-01 | [155]        | [4.19e-01]     | 6.00e+01 |       0.00e+00 |
+---------+----------+----------------+----------+----------------------+--------------+----------------+----------+----------------+

+----------+------------------+---------------------+----------+-----------------+-----------------+----------------+------------------+
|  info.QD | info.RAW_MQandDP | info.ReadPosRankSum | info.SOR | info.NGSEP_NHET | info.NGSEP_NALT | info.NGSEP_AF  | info.TASSEL_NHET |
+----------+------------------+---------------------+----------+-----------------+-----------------+----------------+------------------+
|  float64 | array<int32>     |             float64 |  float64 | array<int32>    | array<int32>    | array<float64> | array<int32>     |
+----------+------------------+---------------------+----------+-----------------+-----------------+----------------+------------------+
| 2.32e+01 | NA               |            0.00e+00 | 3.97e+00 | [0]             | [0]             | [0.00e+00]     | [16]             |
| 2.32e+01 | NA               |            0.00e+00 | 3.97e+00 | [0]             | [0]             | [0.00e+00]     | [16]             |
| 2.32e+01 | NA               |            0.00e+00 | 3.97e+00 | [0]             | [0]             | [0.00e+00]     | [16]             |
+----------+------------------+---------------------+----------+-----------------+-----------------+----------------+------------------+

+------------------+----------------+-----------+----------+--------------+---------------------+------------------+
| info.TASSEL_NALT | info.TASSEL_AF | genome_id | pheno.id | pheno.height | pheno.branch_height | pheno.pod_number |
+------------------+----------------+-----------+----------+--------------+---------------------+---

In [15]:
# call rate before filtering
mt.aggregate_entries(hl.agg.fraction(hl.is_defined(mt.GT)))

2021-08-24 09:40:13 Hail: INFO: Coerced sorted dataset


0.9779972008784086

In [16]:
# final variant and sample count
mt.count()

2021-08-24 09:40:15 Hail: INFO: Coerced sorted dataset


(5234, 166)

## PCAs

In [17]:
pca_eigenvalues, pca_scores, pca_loadings = hl.hwe_normalized_pca(mt.GT, compute_loadings=True)
mt = mt.annotate_cols(pca = pca_scores[mt.genome_id])
p = hl.plot.scatter(mt.pca.scores[0], 
                    mt.pca.scores[1])
show(p)
print([x/sum(pca_eigenvalues) for x in pca_eigenvalues])

2021-08-24 09:40:24 Hail: INFO: Coerced sorted dataset
2021-08-24 09:40:25 Hail: INFO: hwe_normalized_pca: running PCA using 5234 variants.
2021-08-24 09:40:25 Hail: INFO: Coerced sorted dataset
2021-08-24 09:40:26 Hail: INFO: pca: running PCA with 10 components...
2021-08-24 09:40:29 Hail: INFO: Coerced sorted dataset
2021-08-24 09:40:29 Hail: INFO: Coerced sorted dataset


[0.22807032911449915, 0.15280873263213282, 0.13437122419114006, 0.12934191372146497, 0.07230963334679741, 0.06719911347681959, 0.061294231093550186, 0.05550329929387484, 0.05038304784505889, 0.04871847528466229]


In [18]:
#mt = mt.annotate_cols(genome_id_frmt = hl.str(mt.genome_id)
#hl.export_vcf(mt, OUT_VCF)
scores_df = pca_scores.to_pandas()

In [19]:
scores_df.head()

genome_id                                             scores
0        S1  [-0.1392856289153399, 0.41817771532057174, -0....
1       S10  [-0.5943803992544161, -0.5740264022446521, 0.3...
2      S100  [0.006474338429093289, -0.08740784836494055, 0...
3      S102  [0.1306331394015496, -0.0656385561836958, 0.22...
4      S104  [-0.16780284691597294, 0.16876120371697279, 0....

In [20]:
for i in range(1, 11):
    scores_df[f'PC{i}'] = [x[i - 1] for x in scores_df['scores']]

In [21]:
scores_df.drop('scores', axis=1, inplace=True)
scores_df.head()

genome_id       PC1       PC2       PC3       PC4       PC5       PC6  \
0        S1 -0.139286  0.418178 -0.170107  0.045901  0.314681  0.792907   
1       S10 -0.594380 -0.574026  0.323683 -1.037562  0.246027  0.148222   
2      S100  0.006474 -0.087408  0.089134  0.251408  0.240211 -0.251115   
3      S102  0.130633 -0.065639  0.228250  0.124664  0.112927 -0.177768   
4      S104 -0.167803  0.168761  0.001225  0.237359  0.062603  0.146675   

        PC7       PC8       PC9      PC10  
0 -0.237359  0.113218  0.251693  0.283357  
1  0.122373  0.044426 -0.167866 -0.061703  
2 -0.291133  0.088232  0.000784 -0.011808  
3 -0.158527 -0.109306 -0.365951 -0.318269  
4  0.306907 -0.155303 -0.034751  0.030807

In [23]:
scores_df.to_csv(PCA_SCORES)

## LD

In [20]:
ld = hl.ld_matrix(mt.GT.n_alt_alleles(), mt.locus, radius=10e6)

2021-05-05 11:49:34 Hail: INFO: Coerced sorted dataset
2021-05-05 11:49:35 Hail: INFO: Wrote all 2 blocks of 5234 x 166 matrix with block size 4096.


In [21]:
pd_ld = ld.to_numpy()
pd_ld.shape

2021-05-05 11:49:37 Hail: INFO: Coerced sorted dataset


(5234, 5234)

In [22]:
snp_data = mt.rows().to_pandas()
snp_data.head()

2021-05-05 11:49:47 Hail: INFO: Coerced sorted dataset


locus.contig  locus.position alleles  rsid      qual filters info.AC  \
0  contig_1004           28957  [C, T]  None  19975.20    None   [138]   
1  contig_1004           42060  [C, T]  None  21962.31    None   [107]   
2  contig_1004           51238  [C, T]  None  27678.85    None   [110]   
3  contig_1004          147808  [G, A]  None   9465.62    None    [60]   
4  contig_1004          266475  [C, T]  None  20300.58    None   [132]   

   info.AF  info.AN  info.BaseQRankSum  ...  info.QD  info.RAW_MQandDP  \
0  [0.373]      370              0.349  ...    23.23              None   
1  [0.279]      384              0.431  ...    29.20              None   
2  [0.286]      384             -0.411  ...    34.42              None   
3  [0.158]      380              0.180  ...    33.21              None   
4  [0.353]      374             -0.210  ...    30.54              None   

  info.ReadPosRankSum  info.SOR  info.NGSEP_NHET  info.NGSEP_NALT  \
0                 0.0     3.967              [0]              [0]   
1                 0.0     4.174              [4]             [56]   
2                 0.0     3.979              [0]              [0]   
3                 0.0     4.454              [0]              [0]   
4                 0.0     4.530             [12]             [78]   

  info.NGSEP_AF info.TASSEL_NHET  info.TASSEL_NALT  info.TASSEL_AF  
0         [0.0]             [16]              [69]       [1.07692]  
1        [0.33]              [0]               [0]           [0.0]  
2         [0.0]              [7]              [58]      [0.664865]  
3         [0.0]              [3]              [26]      [0.335366]  
4         [0.4]              [0]               [0]           [0.0]  

[5 rows x 30 columns]

In [25]:
out_file = open('/media/array/guar_proj/production_callset/ld_data.tsv', 'w')
for i in range(5234):
    for j in range(5234):
        loc_A = snp_data['locus.contig'][i]
        loc_B = snp_data['locus.contig'][j]
        pos_A = snp_data['locus.position'][i]
        pos_B = snp_data['locus.position'][j]
        AF_A = snp_data['info.AF'][i][0]
        AF_B = snp_data['info.AF'][j][0]
        if loc_A == loc_B:
            print(f'{loc_A}\t{pos_A}\t{AF_A}\t{loc_B}\t{pos_B}\t{AF_B}\t{pd_ld[i,j]}', file=out_file)
out_file.close()

In [20]:
biallelic_dataset = mt.filter_rows(hl.len(mt.alleles) == 2)
tag_snp = hl.ld_prune(biallelic_dataset.GT, r2=0.8, bp_window_size=2000000)

2021-04-15 15:26:52 Hail: INFO: ld_prune: running local pruning stage with max queue size of 729445 variants
2021-04-15 15:26:52 Hail: INFO: Coerced sorted dataset
2021-04-15 15:26:54 Hail: INFO: wrote table with 4910 rows in 1 partition to /tmp/UTBrZNpodEfAsGrgF5ZCgX
    Total size: 147.88 KiB
    * Rows: 147.87 KiB
    * Globals: 11.00 B
    * Smallest partition: 4910 rows (147.87 KiB)
    * Largest partition:  4910 rows (147.87 KiB)
2021-04-15 15:26:54 Hail: INFO: Coerced sorted dataset
2021-04-15 15:26:55 Hail: INFO: Wrote all 2 blocks of 4910 x 166 matrix with block size 4096.
2021-04-15 15:27:07 Hail: INFO: wrote table with 0 rows in 3 partitions to /tmp/4nAmYu8DaZgwTBNiTkwqpZ
    Total size: 58.84 KiB
    * Rows: 63.00 B
    * Globals: 58.78 KiB
    * Smallest partition: 0 rows (21.00 B)
    * Largest partition:  0 rows (21.00 B)


In [21]:
tag_snp.count()

4910

In [22]:
biallelic_dataset.count()

2021-04-15 15:27:08 Hail: INFO: Coerced sorted dataset


(5735, 166)

## ADMIXTURE file formatting

In [10]:
pseudoref = hl.genetics.ReferenceGenome.from_fasta_file('pseudoreference_genome', 
                                    '/media/array/guar_proj/production_callset/GUAR_to_admixture.fasta', 
                                    '/media/array/guar_proj/production_callset/GUAR_to_admixture.fasta.fai')

In [11]:
mt_admix = hl.import_vcf('/media/array/guar_proj/production_callset/GUAR_to_admixture.vcf', 
                         reference_genome=pseudoref)
mt_admix = mt_admix.annotate_cols(genome_id=hl.str(mt_admix.s))
mt_admix = mt_admix.key_cols_by("genome_id")
mt_admix = mt_admix.drop("s")
mt_admix = mt_admix.filter_rows(hl.len(mt_admix.alleles) == 2)
mt_admix.describe()

----------------------------------------
Global fields:
    None
----------------------------------------
Column fields:
    'genome_id': str
----------------------------------------
Row fields:
    'locus': locus<pseudoreference_genome>
    'alleles': array<str>
    'rsid': str
    'qual': float64
    'filters': set<str>
    'info': struct {
        AC: array<int32>, 
        AF: array<float64>, 
        AN: int32, 
        BaseQRankSum: float64, 
        DP: int32, 
        DS: bool, 
        END: int32, 
        ExcessHet: float64, 
        FS: float64, 
        InbreedingCoeff: float64, 
        MLEAC: array<int32>, 
        MLEAF: array<float64>, 
        MQ: float64, 
        MQRankSum: float64, 
        QD: float64, 
        RAW_MQandDP: array<int32>, 
        ReadPosRankSum: float64, 
        SOR: float64, 
        NGSEP_NHET: array<int32>, 
        NGSEP_NALT: array<int32>, 
        NGSEP_AF: array<float64>, 
        TASSEL_NHET: array<int32>, 
        TASSEL_NALT: array<int32

In [15]:
biallelic_dataset = mt_admix.filter_rows(hl.len(mt_admix.alleles) == 2)
pruned_vars = hl.ld_prune(biallelic_dataset.GT, r2=0.2, bp_window_size=2000000)
mt_admix_pruned = mt_admix.filter_rows(hl.is_defined(pruned_vars[mt_admix.row_key]))

2021-04-28 16:22:53 Hail: INFO: ld_prune: running local pruning stage with max queue size of 729445 variants
2021-04-28 16:22:53 Hail: INFO: Coerced sorted dataset
2021-04-28 16:22:55 Hail: INFO: wrote table with 2005 rows in 1 partition to /tmp/BFOfUR517KsePKI2rTyYHD
    Total size: 59.28 KiB
    * Rows: 59.27 KiB
    * Globals: 11.00 B
    * Smallest partition: 2005 rows (59.27 KiB)
    * Largest partition:  2005 rows (59.27 KiB)
2021-04-28 16:22:55 Hail: INFO: Coerced sorted dataset
2021-04-28 16:22:56 Hail: INFO: Wrote all 1 blocks of 2005 x 166 matrix with block size 4096.
2021-04-28 16:23:02 Hail: INFO: wrote table with 0 rows in 1 partition to /tmp/oyVGUgUbIoNBEbOwoUKivX
    Total size: 23.88 KiB
    * Rows: 21.00 B
    * Globals: 23.86 KiB
    * Smallest partition: 0 rows (21.00 B)
    * Largest partition:  0 rows (21.00 B)


In [17]:
hl.export_plink(mt_admix_pruned, 
                output='/media/array/guar_proj/production_callset/GUAR_2of3_AF5pct_hail', 
                ind_id = mt_admix_pruned.genome_id)

2021-04-28 16:23:46 Hail: INFO: Coerced sorted dataset
2021-04-28 16:23:47 Hail: INFO: Coerced sorted dataset
2021-04-28 16:23:47 Hail: INFO: Coerced sorted dataset
2021-04-28 16:23:47 Hail: INFO: Coerced sorted dataset
2021-04-28 16:23:48 Hail: INFO: Coerced sorted dataset
2021-04-28 16:23:49 Hail: INFO: merging 2 files totalling 82.2K...
2021-04-28 16:23:49 Hail: INFO: while writing:
    /media/array/guar_proj/production_callset/GUAR_2of3_AF5pct_hail.bed
  merge time: 83.636ms
2021-04-28 16:23:49 Hail: INFO: merging 1 files totalling 67.6K...
2021-04-28 16:23:49 Hail: INFO: while writing:
    /media/array/guar_proj/production_callset/GUAR_2of3_AF5pct_hail.bim
  merge time: 4.040ms
2021-04-28 16:23:50 Hail: INFO: merging 40 files totalling 2.5K...
2021-04-28 16:23:50 Hail: INFO: while writing:
    /media/array/guar_proj/production_callset/GUAR_2of3_AF5pct_hail.fam
  merge time: 21.492ms
2021-04-28 16:23:50 Hail: INFO: wrote 2005 variants and 166 samples to '/media/array/guar_proj/prod

## GWAS

In [33]:
# rrm = hl.realized_relationship_matrix(mt.GT).to_numpy()  
# i ='height_18'

# model, p = hl.linear_mixed_model(  
#      y = mt.pheno[i],
#      x=[1.0, mt.pca.scores[0], mt.pca.scores[1], mt.sample_qc.r_het_hom_var],
#      k=rrm,
#      p_path=f'{LMM_OUTPUT}/{i}_p.bm',
#      overwrite=True)

In [24]:
mt = hl.sample_qc(mt)

In [25]:
phenotypes = ['height', 'branch_height', 'maturation_pct',
             'pod_number', 'mature_pod_seed_weight']



for i in phenotypes:
    print('\n\n=============')
    print(i)
    print('=============')
    gwas = hl.linear_regression_rows(y = mt.pheno[i], 
                                     x = mt.GT.n_alt_alleles(), 
                                     covariates=[1.0, mt.pca.scores[0], mt.pca.scores[1], mt.sample_qc.r_het_hom_var])
    gwas.export(f'{GWAS_EXPORT}{i}.tsv')
    p = hl.plot.manhattan(gwas.p_value,
                          significance_line = 1e-06)
    show(p)
    p = hl.plot.qq(gwas.p_value, collect_all=True)
    show(p)



height


2021-08-24 09:42:26 Hail: INFO: Coerced sorted dataset
2021-08-24 09:42:27 Hail: INFO: Coerced sorted dataset
2021-08-24 09:42:27 Hail: WARN: 1 of 166 samples have a missing phenotype or covariate.
2021-08-24 09:42:27 Hail: INFO: linear_regression_rows: running on 165 samples for 1 response variable y,
    with input variable x, and 4 additional covariates...
2021-08-24 09:42:28 Hail: INFO: merging 1 files totalling 511.8K...
2021-08-24 09:42:28 Hail: INFO: while writing:
    output_pvals/filtered_gwas_LMM_height.tsv
  merge time: 13.198ms


2021-08-24 09:42:31 Hail: INFO: Ordering unsorted dataset with network shuffle




branch_height


2021-08-24 09:42:33 Hail: INFO: Coerced sorted dataset
2021-08-24 09:42:34 Hail: INFO: Coerced sorted dataset
2021-08-24 09:42:34 Hail: WARN: 1 of 166 samples have a missing phenotype or covariate.
2021-08-24 09:42:34 Hail: INFO: linear_regression_rows: running on 165 samples for 1 response variable y,
    with input variable x, and 4 additional covariates...
2021-08-24 09:42:35 Hail: INFO: merging 1 files totalling 510.8K...
2021-08-24 09:42:35 Hail: INFO: while writing:
    output_pvals/filtered_gwas_LMM_branch_height.tsv
  merge time: 11.221ms


...

2021-08-24 09:42:45 Hail: INFO: Coerced sorted dataset
2021-08-24 09:42:46 Hail: INFO: Coerced sorted dataset
2021-08-24 09:42:46 Hail: WARN: 2 of 166 samples have a missing phenotype or covariate.
2021-08-24 09:42:46 Hail: INFO: linear_regression_rows: running on 164 samples for 1 response variable y,
    with input variable x, and 4 additional covariates...
2021-08-24 09:42:47 Hail: INFO: merging 1 files totalling 511.6K...
2021-08-24 09:42:47 Hail: INFO: while writing:
    output_pvals/filtered_gwas_LMM_pod_number.tsv
  merge time: 9.478ms


2021-08-24 09:42:49 Hail: INFO: Ordering unsorted dataset with network shuffle




mature_pod_seed_weight


2021-08-24 09:42:51 Hail: INFO: Coerced sorted dataset
2021-08-24 09:42:52 Hail: INFO: Coerced sorted dataset
2021-08-24 09:42:52 Hail: WARN: 2 of 166 samples have a missing phenotype or covariate.
2021-08-24 09:42:52 Hail: INFO: linear_regression_rows: running on 164 samples for 1 response variable y,
    with input variable x, and 4 additional covariates...
2021-08-24 09:42:53 Hail: INFO: merging 1 files totalling 512.1K...
2021-08-24 09:42:53 Hail: INFO: while writing:
    output_pvals/filtered_gwas_LMM_mature_pod_seed_weight.tsv
  merge time: 16.976ms


2021-08-24 09:42:56 Hail: INFO: Ordering unsorted dataset with network shuffle
